In [130]:
# https://metadata.geoportaal.ee/geonetwork/srv/est/catalog.search#/metadata/%7B002F8C73-BF14-4F6D-9D4D-56765FDB5E94%7D
ma_tee = "https://inspire.maaamet.ee/arcgis/rest/services/public/tn_rrc/MapServer/exts/InspireFeatureDownload/service?request=GetCapabilities&service=WFS"
# or

# https://avaandmed.eesti.ee/datasets/teeregister
tr_tee = "https://teeregister-api.mnt.ee/teenus/wfs?request=GetCapabilities&service=WFS"

In [131]:
# https://geopython.github.io/OWSLib/usage.html#wfs

from owslib.wfs import WebFeatureService

In [132]:
# one of them is crap
wfs_tr = WebFeatureService(url=tr_tee, version='1.1.0')


In [11]:
wfs_tr.identification.title

'Teeregistri WFS teenus'

In [133]:
import geopandas as gpd
from shapely.geometry import box, Point, LineString, MultiLineString, Polygon

# ul 58.412411, 26.6342694
# lr 58.3440864, 26.792795

# wgs84_bbox = box(26.6342694, 58.3440864, 26.792795, 58.412411)
wgs84_bbox = box(21.41493918814871, 57.47561599021964, 28.256035600482093, 59.83916717456523)

eestbox = gpd.GeoDataFrame({ 'geometry': [wgs84_bbox]}, geometry="geometry", crs=4326)

In [134]:
extent_84 = eestbox.total_bounds
eestbox_3301 = eestbox.to_crs(3301)
extent_3301 = eestbox_3301.total_bounds
eestbox_merc = eestbox.to_crs(3857)
extent_merc = eestbox_merc.total_bounds

In [135]:
list(wfs_tr.contents)

['ms:Muutee',
 'ms:Ramp',
 'ms:Korvalmaantee',
 'ms:Tugimaantee',
 'ms:Pohimaantee',
 'ms:teeosa',
 'ms:n_omand',
 'ms:n_mnta_haldus',
 'ms:n_hoole',
 'ms:n_alusdokumendid_ja_lepingud',
 'ms:n_liigitus',
 'ms:n_rvteed',
 'ms:n_kiiruspiirang',
 'ms:n_katend',
 'ms:n_kate',
 'ms:n_defekt',
 'ms:n_kandevoime',
 'ms:n_tasas',
 'ms:n_tekstuur',
 'ms:n_vork',
 'ms:n_katlai',
 'ms:n_pindam',
 'ms:n_roobas',
 'ms:n_rooprm',
 'ms:n_seisund_suvine',
 'ms:n_seisund_talvine',
 'ms:n_liiklussagedus',
 'ms:n_maantee_valjaehitamise_klass',
 'ms:n_kruusateede_seisukord',
 'ms:n_kulmakerked',
 'ms:n_tolm',
 'ms:n_kergliiklustee',
 'ms:n_murasein',
 'ms:n_piire',
 'ms:n_valgustus',
 'ms:n_loomatoke',
 'ms:n_lumekaitse_hekk',
 'ms:n_tahispostid',
 'ms:n_truup',
 'ms:n_bussipeatus',
 'ms:n_ristmik',
 'ms:n_ristumispunkt',
 'ms:n_liiklussolm',
 'ms:n_solmpunkt',
 'ms:n_mahasoit',
 'ms:n_seade',
 'ms:n_sild',
 'ms:n_sammas',
 'ms:n_parkla',
 'ms:n_rdtyl',
 'ms:n_ylek',
 'ms:n_liiklusmark',
 'ms:n_kandur',
 

In [136]:
(minx, miny, maxx, maxy) = extent_84
(bottom, left, top, right) = extent_3301

In [137]:
from owslib.etree import etree
import pandas as pd

def get_points(xml_tree):
    points = xml_tree.findall("//{http://www.opengis.net/gml}pos")

    for p in points:
        coord = [float(x) for x in p.text.split(" ")]
        if len(coord) == 2:
            yield coord


def basic_fn(featuretype, idx):
    feature_fn = featuretype.replace(":", "__")
    feature_fn = f"{feature_fn}__{idx}.gml"
    return feature_fn


def partial_query(wfs_s, bbox, featuretype, maxfeatures, startindex):

    # bbox = (bottom, left, top, right),
    # srsname='urn:x-ogc:def:crs:EPSG:4326' 
    response = wfs_s.getfeature(typename=featuretype,
                                bbox=bbox,
                                srsname='EPSG:3301',
                                maxfeatures=maxfeatures,
                                startindex=startindex)
    
    feature_fn = basic_fn(featuretype, startindex)
    
    with open(feature_fn, 'wb') as out:
        databytes = response.read()
        data = bytes(databytes)
        out.write( data)
    return feature_fn


def parse_points_orig_xml(gml_file):
    xml_tree = etree.parse(gml_file)
    return get_points(xml_tree)

In [17]:
wfs_tr_layers =  ['ms:Muutee',
                  'ms:Korvalmaantee',
                  'ms:Tugimaantee',
                  'ms:Pohimaantee',
                  'ms:n_parkla',
                 'ms:n_bussipeatus']


In [18]:
# wfs_s, bbox, featuretype, maxfeatures, startindex
tmp_list = partial_query(wfs_s=wfs_tr, bbox=(bottom, left, top, right), featuretype=wfs_tr_layers[5], maxfeatures=50, startindex=0)

In [19]:
tmp_list

'ms__n_bussipeatus__0.gml'

In [20]:
import geopandas as gpd
import os

collector = {}

for l in wfs_tr_layers:
    print(l)
    collector.update({ l: [] })
    
    list_target = 50000
    returned = list_target
    base_count = 0
    
    while returned >= list_target:
        print(f"start {base_count}")
        tmp_file = partial_query(wfs_s=wfs_tr, bbox=(bottom, left, top, right), featuretype=l, maxfeatures=list_target, startindex=base_count)
        print(tmp_file)
        ser1 = gpd.read_file(tmp_file, driver="GML")
        collector[l].append(ser1)
        returned = len(ser1)
        display(ser1.head(2))
        base_count = base_count + returned
        print(f"returned {returned} collected {len(collector[l])}")
        

        if os.path.isfile(tmp_file):
            os.remove(tmp_file)


ms:Muutee
start 0
ms__Muutee__0.gml


c:\dev\conda3\envs\geopy2021a\lib\site-packages\geopandas\geodataframe.py:577: RuntimeWarning: Sequential read of iterator was interrupted. Resetting iterator. This can negatively impact the performance.
  for feature in features_lst:


gml_id  tee_number                                            nimi  \
0  Muutee.27784     7950307                                         Side tn   
1  Muutee.23440     7950599  Hipodroomi tn, ringtee ümber Hipodroomi tn 12a   

   pikkus tee_teeliik_xv tee_teeliik_val inspire_functionalclass on_riigitee  \
0     311            MUU         Muu tee             fourthClass       false   
1     382            MUU         Muu tee             fourthClass       false   

     oid muudetud_kpv                                           geometry  
0  27784   2018-05-23  LINESTRING (6472453.846 659212.454, 6472448.10...  
1  23440   2018-05-23  LINESTRING (6470694.651 662399.741, 6470700.59...

returned 1428 collected 1
ms:Korvalmaantee
start 0
ms__Korvalmaantee__0.gml


c:\dev\conda3\envs\geopy2021a\lib\site-packages\geopandas\geodataframe.py:577: RuntimeWarning: Sequential read of iterator was interrupted. Resetting iterator. This can negatively impact the performance.
  for feature in features_lst:


...

gml_id  tee_number               tee_nimi  soidutee_nr       km  \
0  n_parkla.7072562           3  Jõhvi - Tartu - Valga            1  130.283   
1   n_parkla.540842           3  Jõhvi - Tartu - Valga            1  138.543   

   teeosa  teeosa_meeter par_parklat_xv     par_parklat_val par_parvav_xv  \
0      19          10185              5              tankla             2   
1      22             50              6  motell või kämping             1   

   ... par_parteen_val parklanr                   parkla_nimi parkpind  \
0  ...            None     None  Tartu Astelpaju tn 2a tankla     3300   
1  ...            None     None   Tartu Kantri hotelli parkla      730   

           markus      oid tee_oid teeosa_oid muudetud_kpv  \
0  Prügikast: jah  7072562   15478     102612   2021-04-16   
1  Prügikast: jah   540842   15478     102619   2021-04-16   

                         geometry  
0  POINT (6477233.428 658281.593)  
1  POINT (6471011.485 656552.225)  

[2 rows x 26 columns]

returned 11 collected 1
ms:n_bussipeatus
start 0
ms__n_bussipeatus__0.gml


c:\dev\conda3\envs\geopy2021a\lib\site-packages\geopandas\geodataframe.py:577: RuntimeWarning: Sequential read of iterator was interrupted. Resetting iterator. This can negatively impact the performance.
  for feature in features_lst:


gml_id  tee_number                          tee_nimi  \
0  n_bussipeatus.854730           2  Tallinn - Tartu - Võru - Luhamaa   
1  n_bussipeatus.854731           2  Tallinn - Tartu - Võru - Luhamaa   

   soidutee_nr       km  teeosa  teeosa_meeter    nimi korv_bpkorv_xv  \
0            1  180.767      28           1834  Haigla              1   
1            1  180.776      28           1843  Haigla              1   

  korv_bpkorv_val  ... bpistep_bpistep_xv bpistep_bpistep_val  markus  \
0  kõrvalesõit on  ...                  1         istepink on  Haigla   
1  kõrvalesõit on  ...                  1         istepink on  Haigla   

  viitepunkt viitepunkti_suund_nvps_xv     oid tee_oid teeosa_oid  \
0          5                   PAREMAL  854730   14776     101545   
1          5                   VASAKUL  854731   14776     101545   

  muudetud_kpv                        geometry  
0   2018-05-23  POINT (6472364.050 656682.429)  
1   2018-05-23  POINT (6472355.047 656692.437)  

[2 rows x 36 columns]

returned 28 collected 1


In [21]:
bus = collector['ms:n_bussipeatus'][0]
bus['easting'] = bus.geometry.apply(lambda x: x.y)
bus['northing'] = bus.geometry.apply(lambda x: x.x)
bus['new_point'] = bus.apply(lambda row: Point(row['easting'], row['northing']), axis=1)

In [22]:
bus2 = bus.drop(columns=['geometry']).rename(columns={'new_point': 'geometry'})
bus2 = gpd.GeoDataFrame(bus2, geometry="geometry", crs=3301)

In [23]:
bus2.to_crs(4326).head(2)

gml_id  tee_number                          tee_nimi  \
0  n_bussipeatus.854730           2  Tallinn - Tartu - Võru - Luhamaa   
1  n_bussipeatus.854731           2  Tallinn - Tartu - Võru - Luhamaa   

   soidutee_nr       km  teeosa  teeosa_meeter    nimi korv_bpkorv_xv  \
0            1  180.767      28           1834  Haigla              1   
1            1  180.776      28           1843  Haigla              1   

  korv_bpkorv_val  ...  markus viitepunkt viitepunkti_suund_nvps_xv     oid  \
0  kõrvalesõit on  ...  Haigla          5                   PAREMAL  854730   
1  kõrvalesõit on  ...  Haigla          5                   VASAKUL  854731   

  tee_oid teeosa_oid muudetud_kpv        easting      northing  \
0   14776     101545   2018-05-23  656682.428988  6.472364e+06   
1   14776     101545   2018-05-23  656692.437280  6.472355e+06   

                    geometry  
0  POINT (26.67771 58.36364)  
1  POINT (26.67788 58.36356)  

[2 rows x 38 columns]

In [24]:
bus.head(2)

gml_id  tee_number                          tee_nimi  \
0  n_bussipeatus.854730           2  Tallinn - Tartu - Võru - Luhamaa   
1  n_bussipeatus.854731           2  Tallinn - Tartu - Võru - Luhamaa   

   soidutee_nr       km  teeosa  teeosa_meeter    nimi korv_bpkorv_xv  \
0            1  180.767      28           1834  Haigla              1   
1            1  180.776      28           1843  Haigla              1   

  korv_bpkorv_val  ... viitepunkt viitepunkti_suund_nvps_xv     oid tee_oid  \
0  kõrvalesõit on  ...          5                   PAREMAL  854730   14776   
1  kõrvalesõit on  ...          5                   VASAKUL  854731   14776   

  teeosa_oid muudetud_kpv                        geometry        easting  \
0     101545   2018-05-23  POINT (6472364.050 656682.429)  656682.428988   
1     101545   2018-05-23  POINT (6472355.047 656692.437)  656692.437280   

       northing                             new_point  
0  6.472364e+06  POINT (656682.428988 6472364.050121)  
1  6.472355e+06   POINT (656692.43728 6472355.046938)  

[2 rows x 39 columns]

In [25]:
for l in wfs_tr_layers:
    print(l)

ms:Muutee
ms:Korvalmaantee
ms:Tugimaantee
ms:Pohimaantee
ms:n_parkla
ms:n_bussipeatus


In [114]:
l1 = collector['ms:Muutee'][0][['nimi','pikkus','tee_teeliik_xv', 'geometry']].copy()
l2 = collector['ms:Korvalmaantee'][0][['nimi','pikkus','tee_teeliik_xv', 'geometry']].copy()
l3 = collector['ms:Tugimaantee'][0][['nimi','pikkus','tee_teeliik_xv', 'geometry']].copy()
l4 = collector['ms:Pohimaantee'][0][['nimi','pikkus','tee_teeliik_xv', 'geometry']].copy()

In [115]:
import mapclassify as mc

classifier = mc.NaturalBreaks.make(k=8)

In [116]:
l1['color_class'] = l1[['pikkus']].apply(classifier)

In [117]:
import pyproj
import pyproj

from shapely.geometry import Point
from shapely.ops import transform

wgs84 = pyproj.CRS('EPSG:4326')
utm = pyproj.CRS('EPSG:3301')

reproject = pyproj.Transformer.from_crs(utm, wgs84).transform

def to_wgs(pp):
    utm_point = transform(reproject, pp)
    return utm_point


In [118]:
import itertools

def make_line_points(geom):
    if isinstance(geom, LineString):
        list_x = list(geom.coords.xy[1])
        list_y = list(geom.coords.xy[0])
        lll = list(zip(list_y, list_x))
        
        rrr = to_wgs( LineString(lll) )
        
        list_x = list(rrr.coords.xy[0])
        list_y = list(rrr.coords.xy[1])
        lll = list(zip(list_y, list_x))
        return lll
                    
    elif isinstance(geom, MultiLineString):
        all_lines = []
        for l in geom:
            single = make_line_points(geom)
            all_lines.append(single)
        flattened = list(itertools.chain(*all_lines))
        return flattened
    else:
        return []

In [119]:
l1['geoflat'] = l1.geometry.apply(make_line_points)

In [120]:
l1.loc[0, 'geoflat']

[(26.720966929317857, 58.36353230656534),
 (26.72120466193338, 58.363475603350736),
 (26.721293764007388, 58.36344788647761),
 (26.721562702950326, 58.3633407264616),
 (26.72432515131723, 58.36217267847508),
 (26.724723374433985, 58.36200428848961),
 (26.724825078426363, 58.3619629468873),
 (26.72484672878162, 58.3619541455803),
 (26.724992230706775, 58.36190119313208)]

In [121]:
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
from matplotlib import colors

x = plt.get_cmap("RdPu", 8)

In [122]:
rgb = (int(c * 255) for c in x(8)[:-1])
tuple(rgb)

(73, 0, 106)

In [123]:
l1[['nimi', 'geoflat', 'color_class']].sample(3)

nimi  \
1072                                Adra tn   
974   Turu tn 11, 13, 15, 19 juurdepääsutee   
376                                  Eha tn   

                                                geoflat  color_class  
1072  [(26.727113844108565, 58.398509627221785), (26...            1  
974   [(26.734255236803886, 58.37487590584902), (26....            0  
376   [(26.721357942543822, 58.36842024056344), (26....            3

In [125]:
def make_simple_color(v):
    rgb = (int(c * 255) for c in x(int(v))[:-1])

    return tuple(rgb)

l1["color"] = l1['color_class'].apply(make_simple_color)

In [126]:
l1[['nimi', 'geoflat', 'color', 'color_class']].sample(3)

nimi  \
1037            B. G. Forseliuse tn   
1335  Jänese tn 7, 9 juurdepääsutee   
452   Kaunase pst 55 juurdepääsutee   

                                                geoflat            color  \
1037  [(26.7282366237668, 58.36063790595956), (26.72...  (255, 247, 243)   
1335  [(26.73469244173222, 58.391181646288096), (26....  (255, 247, 243)   
452   [(26.771271774595736, 58.37220147662071), (26....  (252, 220, 216)   

      color_class  
1037            0  
1335            0  
452             1

In [144]:
import pandas as pd
import pydeck as pdk

view_state = pdk.ViewState(latitude=58.37, longitude=26.72, zoom=12, bearing=15, pitch=45, min_zoom=10, max_zoom=15)

layer = pdk.Layer(
    type="PathLayer",
    data=l1[['nimi', 'geoflat', 'color', 'color_class']],
    pickable=True,
    get_color="color",
    width_scale=10,
    width_min_pixels=1,
    get_path="geoflat",
    get_width=2,
)

r = pdk.Deck(layers=[layer], initial_view_state=view_state, map_style="light", tooltip={"text": "{nimi}"})

In [145]:
r.to_html("path_layer.html")

In [144]:
r

{"initialViewState": {"latitude": 58.37, "longitude": 26.72, "zoom": 10}, "layers": [{"@@type": "PathLayer", "data": [{"geoflat": [[60.92312292705681, 0.2983139838963877], [60.92310455522949, 0.29840917494525326], [60.923094117367455, 0.2984660584312521], [60.923090374237546, 0.29851478937882187]], "geometry": {"coordinates": [[6474958.731, 659778.834], [6474947.642, 659790.921], [6474941.094, 659798.192], [6474936.239, 659804.884]], "type": "LineString"}, "nimi": "Roosi tn, Kivi tn 44 juurdep\u00e4\u00e4sutee", "pikkus": 36, "tee_teeliik_xv": "MUU"}, {"geoflat": [[60.90160339511767, 0.30277153966497605], [60.90148528323469, 0.3026271210470766], [60.901263741611025, 0.3023521485195825], [60.900959003342955, 0.30197390631169896], [60.90073100828494, 0.30169092362658834], [60.900640458425805, 0.30158253920400513], [60.900367662306344, 0.30124043812197887], [60.89999980037739, 0.3007796372681066], [60.899706447716845, 0.3004156890856891], [60.899058906487745, 0.2996074154762065], [60.89896659365173, 0.2994979948529276], [60.89860416209737, 0.29904809467577037], [60.89826663351682, 0.29862910762305506], [60.897922634295135, 0.2981992089119963], [60.897839083160825, 0.29809461109511237], [60.897605364790756, 0.29780262452340467], [60.89747210692023, 0.2976360520761354], [60.89741504671745, 0.29756634882300986], [60.89736370427693, 0.2975036010999562], [60.89725035223612, 0.2973642338809979], [60.89715537013758, 0.29724679209871663], [60.897113022168455, 0.2971893449033939]], "geometry": {"coordinates": [[6471440.944, 658505.208], [6471436.57, 658473.87], [6471428.727, 658414.5], [6471417.939, 658332.833], [6471409.867, 658271.733], [6471406.307, 658248.044], [6471396.959, 658174.431], [6471384.307, 658075.239], [6471373.906, 657996.645], [6471351.379, 657822.45], [6471347.654, 657798.454], [6471334.824, 657701.315], [6471322.875, 657610.85], [6471310.951, 657518.235], [6471308.071, 657495.714], [6471299.961, 657432.803], [6471295.345, 657396.92], [6471293.225, 657381.789], [6471291.32, 657368.17], [6471287.188, 657337.982], [6471283.784, 657312.591], [6471282.716, 657300.537]], "type": "LineString"}, "nimi": "Aardla tn (Raudtee tn - Ringtee tn)", "pikkus": 1246, "tee_teeliik_xv": "MUU"}, {"geoflat": [[60.90654118081951, 0.3054731937785574], [60.90664526993428, 0.30546117283945545], [60.90683777198267, 0.30544464679218675], [60.90692635874045, 0.3054329526875708], [60.906951074675945, 0.30543950384129714], [60.906961513251346, 0.30545104987885385], [60.90705761120492, 0.30560703704651776], [60.907117126745206, 0.30570365156741425], [60.90713044222443, 0.30572970011559275], [60.9071343205981, 0.3057444442066576], [60.90714363935126, 0.30579636330150345], [60.90714798802226, 0.3058576634871009], [60.90714454456054, 0.3058743557727265], [60.90712355628237, 0.30590526734788204]], "geometry": {"coordinates": [[6471918.752, 659334.33], [6471934.923, 659341.864], [6471964.325, 659356.62], [6471978.217, 659362.821], [6471981.225, 659365.966], [6471981.719, 659368.56], [6471981.872, 659399.605], [6471981.966, 659418.833], [6471981.595, 659423.774], [6471980.854, 659426.245], [6471977.615, 659434.56], [6471972.825, 659443.785], [6471970.849, 659445.885], [6471965.069, 659448.473]], "type": "LineString"}, "nimi": "Ropka tn 6 juurdep\u00e4\u00e4sutee", "pikkus": 161, "tee_teeliik_xv": "MUU"}, {"geoflat": [[60.90041766135819, 0.30426929451595797], [60.90037627091671, 0.3042817682271963], [60.900356588106355, 0.30429079229523975], [60.90027238732204, 0.30433899021256905], [60.900179010569005, 0.30439837378534335], [60.900081815906766, 0.3044645183556818], [60.899963538797145, 0.3045407033325262], [60.899431097574094, 0.3048779788002111]], "geometry": {"coordinates": [[6471136.387, 658615.608], [6471129.276, 658613.722], [6471125.621, 658613.271], [6471109.137, 658612.725], [6471090.332, 658612.975], [6471070.375, 658613.86], [6471046.47, 658614.316], [6470939.361, 658615.55]], "type": "LineString"}, "nimi": "Pohla tn", "pikkus": 198, "tee_teeliik